# This notebook contains code used for 
## 1. Implementing the trading strategy given and generating results
## 2. Tracking the equity value throughout the year based on entry positions

In [39]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px

The datasets generated in the data_cleaning notebook are imported for use. As size is reduced, we can proceed to pandas without dask.

In [40]:
options_call = pd.read_csv('options_ce.csv')
options_put = pd.read_csv('options_pe.csv')
futures = pd.read_csv('futures.csv')

Exporting a CSV reformats the datetime values to python object. Thus, I will convert them back to datetime with the required format.

In [41]:
options_call['Datetime'] = pd.to_datetime(options_call['Datetime'], format = '%Y-%m-%d')
options_call['Expiry'] = pd.to_datetime(options_call['Expiry'], format = '%Y-%m-%d')
options_put['Datetime'] = pd.to_datetime(options_put['Datetime'], format = '%Y-%m-%d')
options_put['Expiry'] = pd.to_datetime(options_put['Expiry'], format = '%Y-%m-%d')

futures['Date'] = pd.to_datetime(futures['Date'], format = '%Y-%m-%d')
futures['Expiry'] = pd.to_datetime(futures['Expiry'], format = '%Y-%m-%d')
futures['Time'] = pd.to_datetime(futures['Time'], format = '%H:%M:%S')

futures['Datetime'] = pd.to_datetime(futures['Date'].astype(str) + ' ' + futures['Time'].dt.time.astype(str))
col_order = ['Datetime', 'Close', 'Expiry']
futures = futures.drop(['Date', 'Time'], axis = 1).reindex(columns = col_order)

## 1. Implementing the strategy
This part contains the relevant function definitions used to implement the strategy.

## Function 1:
This function calculates strike prices based on an input future price and the away_wing percentages and outputs them as a 3-element tuple.

In [42]:
def strike_calc(future_price, away_wing_perc_call=2, away_wing_perc_put=2): #applicable to both call and put
    ATM_strike = round(future_price, -2) # rounding to nearest hundreds, as option strikes change in hundreds
    call_factor = 1 + (away_wing_perc_call/100)
    put_factor = 1 - (away_wing_perc_put/100)
    OTM_call_strike = round(ATM_strike * call_factor, -2)
    OTM_put_strike = round(ATM_strike * put_factor, -2)
    
    return ATM_strike, OTM_call_strike, OTM_put_strike

## Function 2:
This function takes an input dataframe and a date along with the relevant strike prices. Based on the given df and date, it calculates the option strikes nearest to the given strikes, and outputs the corresponding tickers of the options. This function needs to be applied separately to both call and put option datasets, unlike the previous function.

In [43]:
def closest_strikes(df, datetime_input, ATM_strike, OTM_strike): #applicable to either call or put, need to specify df accordingly
    
    filtered_df = df[df['Datetime'] == pd.to_datetime(datetime_input)]

    strikes = np.array(filtered_df['Strike'])

    atm_index = np.argmin(np.abs(strikes - ATM_strike))
    otm_index = np.argmin(np.abs(strikes - OTM_strike))

    atm_ticker = filtered_df.iloc[atm_index]['Ticker']
    otm_ticker = filtered_df.iloc[otm_index]['Ticker']
    
    return atm_ticker, otm_ticker

## Function 3:
Perhaps the most important of the lot. This function identifies the entry and exit points in call and put options datasets, given a ticker (obtained from the previous function). It allows generic values for stop_loss and target to find the optimum allocation, though their default values are set at 30% and 80% respectively, according to the assignment. The function also outputs number of profitable or loss making trades made.

In [44]:
def entry_exit_identifier(df, ATM_ticker, OTM_ticker, stop_loss=30, target=80): #applicable to either call or put, need to specify df accordingly
    short_psn_df = df[df['Ticker'] == ATM_ticker].copy()
    long_psn_df = df[df['Ticker'] == OTM_ticker].copy()
    
    short_psn_df = short_psn_df.reset_index(drop = True)
    long_psn_df = long_psn_df.reset_index(drop = True)
    
    short_psn_df['Status'] = '0'
    long_psn_df['Status'] = '0'
    
    short_psn_df.loc[0, 'Status'] = 'S_En'
    long_psn_df.loc[0, 'Status'] = 'L_En'
    
    short_En_price = short_psn_df.loc[0, 'Close']
    long_En_price = long_psn_df.loc[0, 'Close']
    short_Ex_price = short_En_price
    long_Ex_price = long_En_price
    
    stop_loss_short = 1 + (stop_loss/100)
    stop_loss_long = 1 - (stop_loss/100)
    target_short = 1 - (target/100)
    target_long = 1 + (target/100)
    
    short_exit_flag = 0
    long_exit_flag = 0
    
    prof_trade = 0
    loss_trade = 0

    for i in range(len(short_psn_df.index)):
        short_current_close = short_psn_df.loc[i, 'Close']
        short_ratio = short_current_close / short_En_price 
        
        if ((short_ratio >= stop_loss_short or short_ratio <= target_short) and not(short_exit_flag)):
            short_psn_df.loc[i, 'Status'] = 'S_Ex'
            short_exit_flag = 1
            short_Ex_price = short_psn_df.loc[i, 'Close']
            if (short_ratio >= stop_loss_short):
                loss_trade += 1
            else:
                prof_trade += 1
            break
    
    for i in range(len(long_psn_df.index)):
        long_current_price = long_psn_df.loc[i, 'Close']
        long_ratio = long_current_price / long_En_price
        
        if ((long_ratio <= stop_loss_long or long_ratio >= target_long) and not(long_exit_flag)):
            long_psn_df.loc[i, 'Status'] = 'L_Ex'
            long_exit_flag = 1
            long_Ex_price = long_psn_df.loc[i, 'Close'] 
            if (long_ratio <= stop_loss_long):
                loss_trade += 1
            else:
                prof_trade += 1
            break
            
    if (not(short_exit_flag)):
        short_psn_df.iloc[-1, short_psn_df.columns.get_loc('Status')] = 'S_Ex'
        short_Ex_price = short_psn_df.iloc[-1, short_psn_df.columns.get_loc('Close')]
        if (short_Ex_price > short_En_price):
            loss_trade += 1
        else:
            prof_trade += 1
    if (not(long_exit_flag)):
        long_psn_df.iloc[-1, long_psn_df.columns.get_loc('Status')] = 'L_Ex'
        long_Ex_price = long_psn_df.iloc[-1, long_psn_df.columns.get_loc('Close')]
        if (long_Ex_price < long_En_price):
            loss_trade += 1
        else:
            prof_trade += 1
        
    return short_psn_df, long_psn_df, prof_trade, loss_trade
            

## Function 4:
As mentioned in the previous notebook, there will be a need to consolidate data for call and put options. This function does exactly that, by taking dataframes marked with entry and exit points as input, and outputs a one row dataframe containing the relevant values. This one-row dataframe contains data for only one day.

In [45]:
def consolidate(call_short_df, call_long_df, put_short_df, put_long_df, futures, future_price, 
                ATM_strike, OTM_call_strike, OTM_put_strike, call_prof, call_loss, put_prof, put_loss):
    
    call_short = call_short_df[call_short_df['Status'] != '0'].reset_index(drop=True)
    call_long = call_long_df[call_long_df['Status'] != '0'].reset_index(drop=True)
    put_short = put_short_df[put_short_df['Status'] != '0'].reset_index(drop=True)
    put_long = put_long_df[put_long_df['Status'] != '0'].reset_index(drop=True)
    
    result = pd.DataFrame(columns=['Date', 'Expiry', 'Ce_En_Date', 'Pe_En_Date', 'Ce_Ex_Date', 'Pe_Ex_Date', 'Fut_En_Price', 
                                    'ATM_strike', 'Ce_short_strike', 'Pe_short_strike', 'Ce_long_strike', 'Pe_long_strike', 
                                    'Ce_short_En_price', 'Ce_short_Ex_price', 'Pe_short_En_price', 'Pe_short_Ex_price', 
                                    'Ce_long_En_price', 'Ce_long_Ex_price', 'Pe_long_En_price', 'Pe_long_Ex_price', 
                                    'prof_trade', 'loss_trade'])
    
    result.loc[0, 'Date'] = call_short.loc[0, 'Datetime'].date()
    result.loc[0, 'Expiry'] = pd.to_datetime(call_short.loc[0, 'Expiry']).date()
    
    result.loc[0, 'Ce_En_Date'] = call_short.loc[0, 'Datetime']
    result.loc[0, 'Pe_En_Date'] = put_short.loc[0, 'Datetime']
    
    a = call_short.loc[1, 'Datetime']
    b = call_long.loc[1, 'Datetime']
    c = put_short.loc[1, 'Datetime']
    d = put_long.loc[1, 'Datetime']
    
    result.loc[0, 'Ce_Ex_Date'] = a if (a > b) else b
    result.loc[0, 'Pe_Ex_Date'] = c if (c > d) else d
    
    result.loc[0, 'Fut_En_Price'] = future_price
    result.loc[0, 'ATM_strike'] = ATM_strike
    result.loc[0, 'Ce_short_strike'] = ATM_strike
    result.loc[0, 'Pe_short_strike'] = ATM_strike
    result.loc[0, 'Ce_long_strike'] = OTM_call_strike
    result.loc[0, 'Pe_long_strike'] = OTM_put_strike
    
    result.loc[0, 'Ce_short_En_price'] = call_short.loc[0, 'Close']
    result.loc[0, 'Ce_short_Ex_price'] = call_short.loc[1, 'Close']
    result.loc[0, 'Pe_short_En_price'] = put_short.loc[0, 'Close']
    result.loc[0, 'Pe_short_Ex_price'] = put_short.loc[1, 'Close']

    result.loc[0, 'Ce_long_En_price'] = call_long.loc[0, 'Close']
    result.loc[0, 'Ce_long_Ex_price'] = call_long.loc[1, 'Close']
    result.loc[0, 'Pe_long_En_price'] = put_long.loc[0, 'Close']
    result.loc[0, 'Pe_long_Ex_price'] = put_long.loc[1, 'Close']
    
    result.loc[0, 'prof_trade'] = call_prof + put_prof
    result.loc[0, 'loss_trade'] = call_loss + put_loss
    
    return result

## Function 5:
The above discussed functions are all made with the assumption that data for only one day at a time is provided. Thus, this function outputs the day-wise data as a dictionary with dates as keys, which can be accessed using the unique_entry_dates list (also a function output).

In [46]:
def extract_daily_data(options_call):

    options_call['Datetime'] = pd.to_datetime(options_call['Datetime'])

    unique_entry_dates = options_call['Datetime'].dt.date.unique()
    unique_exit_dates = options_call['Expiry'].dt.date.unique()

    daily_data = {}

    for date in unique_entry_dates:
        daily_data[date] = options_call[options_call['Datetime'].dt.date == date].copy()
    
    return daily_data, unique_entry_dates, unique_exit_dates

## Function 6:
This is the overall function used to implement the given strategy. The flow is as follows: <br>
extract day-wise data --> calculate strike prices --> find the closest strike tickers --> identify entry and exit points --> consolidate data. <br>
function 5 --> function 1 --> function 2 --> function 3 --> function 4 <br>
The final output is an overall_results dataframe of almost the same format as given in the sample.

In [50]:
def strategy_implement(futures, options_call, options_put, stop_loss=30, target=80, away_wing_call=2, away_wing_put=2):
    call_daywise, unique_entry_dates, uniqu_exit_dates = extract_daily_data(options_call)
    put_daywise = extract_daily_data(options_put)[0]
    
    overall_result = pd.DataFrame(columns=['Date', 'Expiry', 'Ce_En_Date', 'Pe_En_Date', 'Ce_Ex_Date', 'Pe_Ex_Date', 'Fut_En_Price', 
                                    'ATM_strike', 'Ce_short_strike', 'Pe_short_strike', 'Ce_long_strike', 'Pe_long_strike', 
                                    'Ce_short_En_price', 'Ce_short_Ex_price', 'Pe_short_En_price', 'Pe_short_Ex_price', 
                                    'Ce_long_En_price', 'Ce_long_Ex_price', 'Pe_long_En_price', 'Pe_long_Ex_price', 
                                    'prof_trade', 'loss_trade'])
    
    for index, row in futures.iterrows():
        curr_date = row['Datetime'].date()
        call_curr_date = call_daywise[unique_entry_dates[index]]
        put_curr_date = put_daywise[unique_entry_dates[index]]
        
        future_price = futures.loc[index, 'Close']
        strikes = strike_calc(future_price, away_wing_perc_call = away_wing_call, away_wing_perc_put = away_wing_put)
        
        call_tickers = closest_strikes(call_curr_date, futures.loc[index, 'Datetime'], strikes[0], strikes[1])
        put_tickers = closest_strikes(put_curr_date, futures.loc[index, 'Datetime'], strikes[0], strikes[2])
        
        call_short_df, call_long_df, call_prof, call_loss = entry_exit_identifier(call_curr_date, call_tickers[0], call_tickers[1],
                                                                                 stop_loss=stop_loss, target=target)
        put_short_df, put_long_df, put_prof, put_loss = entry_exit_identifier(put_curr_date, put_tickers[0], put_tickers[1],
                                                                             stop_loss=stop_loss, target=target)
        
        curr_day_result = consolidate(call_short_df, call_long_df, put_short_df, put_long_df, futures, future_price, strikes[0],
                                      strikes[1], strikes[2], call_prof, call_loss, put_prof, put_loss)
        
        overall_result = pd.concat([overall_result, curr_day_result], ignore_index=True)
        
    return overall_result

In [51]:
overall_result = strategy_implement(futures, options_call, options_put, stop_loss=30, target=80, away_wing_call=2, away_wing_put=2)


In [52]:
overall_result

Date      Expiry           Ce_En_Date           Pe_En_Date  \
0    2017-01-02  2017-01-05  2017-01-02 10:30:00  2017-01-02 10:30:00   
1    2017-01-03  2017-01-05  2017-01-03 10:30:00  2017-01-03 10:30:00   
2    2017-01-04  2017-01-05  2017-01-04 10:30:00  2017-01-04 10:30:00   
3    2017-01-05  2017-01-05  2017-01-05 10:30:00  2017-01-05 10:30:00   
4    2017-01-06  2017-01-12  2017-01-06 10:30:00  2017-01-06 10:30:00   
..          ...         ...                  ...                  ...   
241  2017-12-22  2017-12-28  2017-12-22 10:30:00  2017-12-22 10:30:00   
242  2017-12-26  2017-12-28  2017-12-26 10:30:00  2017-12-26 10:30:00   
243  2017-12-27  2017-12-28  2017-12-27 10:30:00  2017-12-27 10:30:00   
244  2017-12-28  2017-12-28  2017-12-28 10:30:00  2017-12-28 10:30:00   
245  2017-12-29  2018-01-04  2017-12-29 10:30:00  2017-12-29 10:30:00   

              Ce_Ex_Date           Pe_Ex_Date Fut_En_Price ATM_strike  \
0    2017-01-02 15:20:00  2017-01-02 10:50:00     18067.95    18100.0   
1    2017-01-03 15:20:00  2017-01-03 15:20:00      18107.0    18100.0   
2    2017-01-04 15:20:00  2017-01-04 13:04:00     18048.05    18000.0   
3    2017-01-05 11:51:00  2017-01-05 13:56:00      18079.7    18100.0   
4    2017-01-06 15:20:00  2017-01-06 15:20:00      18340.0    18300.0   
..                   ...                  ...          ...        ...   
241  2017-12-22 15:20:00  2017-12-22 15:20:00     25640.05    25600.0   
242  2017-12-26 15:20:00  2017-12-26 15:20:00      25611.0    25600.0   
243  2017-12-27 15:17:00  2017-12-27 14:23:00     25710.05    25700.0   
244  2017-12-28 15:10:00  2017-12-28 15:15:00      25471.7    25500.0   
245  2017-12-29 15:20:00  2017-12-29 15:20:00      25573.0    25600.0   

    Ce_short_strike Pe_short_strike  ... Ce_short_En_price Ce_short_Ex_price  \
0           18100.0         18100.0  ...             89.95             73.95   
1           18100.0         18100.0  ...              90.3             61.65   
2           18000.0         18000.0  ...             94.45             30.05   
3           18100.0         18100.0  ...              20.0              26.8   
4           18300.0         18300.0  ...             129.0             109.7   
..              ...             ...  ...               ...               ...   
241         25600.0         25600.0  ...            160.05             173.1   
242         25600.0         25600.0  ...            115.55             139.6   
243         25700.0         25700.0  ...             89.15              15.9   
244         25500.0         25500.0  ...              41.4               7.4   
245         25600.0         25600.0  ...             103.6              93.1   

    Pe_short_En_price Pe_short_Ex_price Ce_long_En_price Ce_long_Ex_price  \
0              171.45             227.3            16.15            10.55   
1              136.55             190.0             12.1             7.75   
2                82.0            107.55              6.4             4.45   
3               79.05              14.5             0.15              0.1   
4               137.0            143.75             19.5             13.5   
..                ...               ...              ...              ...   
241             125.9             99.75             14.4            13.85   
242             101.5              65.3             5.75              6.0   
243              75.0             131.0             2.45              1.7   
244              77.1               9.5             0.15              0.1   
245            177.75            177.25             8.95              6.1   

    Pe_long_En_price Pe_long_Ex_price prof_trade loss_trade  
0              32.35            58.65          2          2  
1               21.6             19.5          1          3  
2                6.0             3.65          1          3  
3               0.35              0.2          1          3  
4              30.55             31.2          2          2  

In [53]:
overall_result.to_csv('overall_result.csv', index=False)

The results dataframe is exported as csv. Some part of the processing will now be done using Excel workbook, as the remaining part is fairly trivial. <br>
It may be noted that here exporting to excel is possible due to a small dataset. This may not be possible with larger datasets.

## 2. Tracking the movement of overall equity value

## Function 7: 
It was noticed during pre-processing that call and put options datasets did not have the same number of datapoints. This implies that there may be data missing for some timestamps, or some extra tickers in put options. In case it is the former, for the next part it needs to be ensured that values for missing timestamps are filled. One possibility is to fill in the last valid values, which is followed in the below function. <br>
The function takes in a dataframe and ensures all timestamps from 10:30:00 to 15:20:00 at increments of 1 minute are filled.

In [54]:
def fill_missing_timestamps(df):

    expected_times = pd.date_range("10:30:00", "15:20:00", freq="T").time

    df['Time'] = df['Datetime'].apply(lambda x: x.time())

    expected_times_series = pd.Series(expected_times)

    missing_times = expected_times_series[~expected_times_series.isin(df['Time'])]

    missing_rows = pd.DataFrame({'Time': missing_times})
    missing_rows['Gain'] = df['Gain'].iloc[-1]  # Fill with the last valid gain value

    df = pd.concat([df, missing_rows], ignore_index=True)

    df.sort_values(by='Time', inplace=True)
    
    df = df.drop(['Time'], axis = 1).reset_index(drop=True)
    return df

## Function 8:
This function takes in a dataframe and the trade position (ie, long or short), and outputs a timeseries data of the gain for that position. The dataframe feeded here needs to have entry and exit points marked, so the output of function 3 can be used.

In [84]:
def position_gain(df, position):
    gain = 0
    gain_df = pd.DataFrame(columns=['Datetime', 'Gain'])
    for i in range(len(df.index)):
        curr_gain_df = pd.DataFrame(columns=['Datetime', 'Gain'])
        curr_gain_df.loc[i, 'Datetime'] = df.loc[i, 'Datetime']
        if i == 0:
            initial_close = df.loc[0, 'Close']
            gain = 0
        else:
            curr_close = df.loc[i, 'Close']
            if position == 'short':
                gain = initial_close - curr_close
            elif position == 'long':
                gain = curr_close - initial_close
                
        curr_gain_df.loc[i, 'Gain'] = gain
        gain_df = pd.concat([gain_df, curr_gain_df], ignore_index=True)
        
    gain_df = fill_missing_timestamps(gain_df)

    return gain_df

## Function 9:
This function again does the job of consolidating. It takes in 4 dataframes (for call/put and short/long) and outputs a consolidated dataframe containing the timeseries gain for all positions. 

In [85]:
def daily_gain(call_short_df, call_long_df, put_short_df, put_long_df):
    call_short_gain = position_gain(call_short_df, 'short')
    call_long_gain = position_gain(call_long_df, 'long')
    put_short_gain = position_gain(put_short_df, 'short')
    put_long_gain = position_gain(put_long_df, 'long')
    
    ovr_gain = pd.DataFrame(columns = ['Datetime', 'Gain_call_short', 'Gain_call_long', 'Gain_put_short', 'Gain_put_long'])
    ovr_gain['Datetime'] = call_short_gain['Datetime']
    ovr_gain['Gain_call_short'] = call_short_gain['Gain']
    ovr_gain['Gain_call_long'] = call_long_gain['Gain']
    ovr_gain['Gain_put_short'] = put_short_gain['Gain']
    ovr_gain['Gain_put_long'] = put_long_gain['Gain']
    
    ovr_gain['Pfolio_gain'] = ovr_gain['Gain_call_short'] + ovr_gain['Gain_call_long'] + ovr_gain['Gain_put_short'] + ovr_gain['Gain_put_long']

    return ovr_gain

## Function 10:
Finally, this function consolidates the 3 previous functions defined. It takes in the relevant data and conditions associated with the trading strategy. The output is an overall dataframe which has the Portfolio gain for all timestamps when the trades are active.

In [86]:
def pfolio_gain(futures, options_call, options_put, stop_loss=30, target=80, away_wing_call=2, away_wing_put=2):
    call_daywise, unique_entry_dates, uniqu_exit_dates = extract_daily_data(options_call)
    put_daywise = extract_daily_data(options_put)[0]
    
    gain_results = pd.DataFrame(columns = ['Datetime', 'Gain_call_short', 'Gain_call_long', 'Gain_put_short', 'Gain_put_long'])
    
    for index, row in futures.iterrows():
        curr_date = row['Datetime'].date()
        call_curr_date = call_daywise[unique_entry_dates[index]]
        put_curr_date = put_daywise[unique_entry_dates[index]]
        
        future_price = futures.loc[index, 'Close']
        strikes = strike_calc(future_price, away_wing_perc_call = away_wing_call, away_wing_perc_put = away_wing_put)
        
        call_tickers = closest_strikes(call_curr_date, futures.loc[index, 'Datetime'], strikes[0], strikes[1])
        put_tickers = closest_strikes(put_curr_date, futures.loc[index, 'Datetime'], strikes[0], strikes[2])
        
        call_short_df, call_long_df, call_prof, call_loss = entry_exit_identifier(call_curr_date, call_tickers[0], call_tickers[1],
                                                                                 stop_loss=stop_loss, target=target)
        put_short_df, put_long_df, put_prof, put_loss = entry_exit_identifier(put_curr_date, put_tickers[0], put_tickers[1],
                                                                             stop_loss=stop_loss, target=target)
        
        curr_day_gain = daily_gain(call_short_df, call_long_df, put_short_df, put_long_df)
        
        gain_results = pd.concat([gain_results, curr_day_gain], ignore_index=True)
        
    return gain_results

In [87]:
gain_results = pfolio_gain(futures, options_call, options_put, stop_loss=30, target=80, away_wing_call=2, away_wing_put=2)


In [88]:
gain_results

Datetime Gain_call_short Gain_call_long Gain_put_short  \
0      2017-01-02 10:30:00               0              0              0   
1      2017-01-02 10:31:00            6.45          -1.05          -13.5   
2      2017-01-02 10:32:00            3.45          -0.65          -8.55   
3      2017-01-02 10:33:00             5.7           -0.9         -10.55   
4      2017-01-02 10:34:00             7.6           -1.7         -13.15   
...                    ...             ...            ...            ...   
71581  2017-12-29 15:16:00             9.6          -2.95          -2.25   
71582  2017-12-29 15:17:00            9.85          -2.95          -1.25   
71583  2017-12-29 15:18:00            7.75           -2.8           2.75   
71584  2017-12-29 15:19:00            10.5           -3.2           -0.3   
71585  2017-12-29 15:20:00            10.5           -3.0            0.5   

      Gain_put_long Pfolio_gain  
0                 0           0  
1              3.55       -4.55  
2               2.4       -3.35  
3              3.85        -1.9  
4               3.3       -3.95  
...             ...         ...  
71581          -1.9         2.5  
71582          -1.8        3.85  
71583          -2.8         4.9  
71584          -2.3         4.7  
71585         -2.25        5.75  

[71586 rows x 6 columns]

Note: A benefit of generating this data is that the gains of various positions can be plotted and compared for a quick visual inspection of which position contributed more to positive returns, and which positions were predominantly loss-making.

## Now, the updated overall results file is imported back again. 
To track the movement of equity, I will add the day's starting capital to the portfolio gain for a particular day. This will be done for all days. The motive behind this step is to accurately find the drawdowns associated with each day. <br>
The overall portfolio drawdown can be simply computed using the Total_Capital_Return values, which is done in a separate notebook.

In [89]:
overall_result_updated = pd.read_csv('overall_result.csv')
overall_result_updated

Date      Expiry     En_Date        Ce_En_Date        Pe_En_Date  \
0    02-01-2017  05-01-2017  02-01-2017  02-01-2017 10:30  02-01-2017 10:30   
1    03-01-2017  05-01-2017  03-01-2017  03-01-2017 10:30  03-01-2017 10:30   
2    04-01-2017  05-01-2017  04-01-2017  04-01-2017 10:30  04-01-2017 10:30   
3    05-01-2017  05-01-2017  05-01-2017  05-01-2017 10:30  05-01-2017 10:30   
4    06-01-2017  12-01-2017  06-01-2017  06-01-2017 10:30  06-01-2017 10:30   
..          ...         ...         ...               ...               ...   
241  22-12-2017  28-12-2017  31-08-2017  22-12-2017 10:30  22-12-2017 10:30   
242  26-12-2017  28-12-2017  01-09-2017  26-12-2017 10:30  26-12-2017 10:30   
243  27-12-2017  28-12-2017  02-09-2017  27-12-2017 10:30  27-12-2017 10:30   
244  28-12-2017  28-12-2017  03-09-2017  28-12-2017 10:30  28-12-2017 10:30   
245  29-12-2017  04-01-2018  04-09-2017  29-12-2017 10:30  29-12-2017 10:30   

           Ce_Ex_Date        Pe_Ex_Date  Fut_En_Price  ATM_Strike  \
0    02-01-2017 15:20  02-01-2017 10:50      18067.95       18100   
1    03-01-2017 15:20  03-01-2017 15:20      18107.00       18100   
2    04-01-2017 15:20  04-01-2017 13:04      18048.05       18000   
3    05-01-2017 11:51  05-01-2017 13:56      18079.70       18100   
4    06-01-2017 15:20  06-01-2017 15:20      18340.00       18300   
..                ...               ...           ...         ...   
241  22-12-2017 15:20  22-12-2017 15:20      25640.05       25600   
242  26-12-2017 15:20  26-12-2017 15:20      25611.00       25600   
243  27-12-2017 15:17  27-12-2017 14:23      25710.05       25700   
244  28-12-2017 15:10  28-12-2017 15:15      25471.70       25500   
245  29-12-2017 15:20  29-12-2017 15:20      25573.00       25600   

     Ce_Short_Strike  ...  Ce_Long_En_Price  Ce_Long_Ex_Price  \
0              18100  ...             16.15             10.55   
1              18100  ...             12.10              7.75   
2              18000  ...              6.40              4.45   
3              18100  ...              0.15              0.10   
4              18300  ...             19.50             13.50   
..               ...  ...               ...               ...   
241            25600  ...             14.40             13.85   
242            25600  ...              5.75              6.00   
243            25700  ...              2.45              1.70   
244            25500  ...              0.15              0.10   
245            25600  ...              8.95              6.10   

     Pe_Long_En_Price  Pe_Long_Ex_Price  Returns_Abs  Quantity  Lot_Size  \
0               32.35             58.65       -19.15         3        25   
1               21.60             19.50       -31.25         3        25   
2                6.00              3.65        34.55         3        25   
3                0.35              0.20        57.55         3        25   
4               30.55             31.20         7.20         3        25   
..                ...               ...          ...       ...       ...   
241             21.25             15.20         6.50         3        25   
242             10.35              7.10         9.15         3        25   
243              4.50             11.25        23.25         3        25   
244              1.05              0.70       101.20         3        25   
245             24.45             22.20         5.90         3        25   

     Total_Abs_Return  Total_Capital_Return  Total_Pct_Return  
0            -1436.25             998563.75         -0.143625  
1            -2343.75             996220.00         -0.234712  
2             2591.25             998811.25          0.260108  
3             4316.25            1003127.50          0.432139  
4              540.00            1003667.50          0.053832  
..                ...                   ...               ...  
241            487.50            1084217.50          0.044984  
242            686.25      

In [90]:
overall_result_updated['Date'] = pd.to_datetime(overall_result_updated['Date'], format='%d-%m-%Y')
overall_result_updated['Expiry'] = pd.to_datetime(overall_result_updated['Expiry'], format='%d-%m-%Y')
overall_result_updated['En_Date'] = pd.to_datetime(overall_result_updated['En_Date'], format='%d-%m-%Y')
overall_result_updated['Ce_En_Date'] = pd.to_datetime(overall_result_updated['Ce_En_Date'], format='%d-%m-%Y %H:%M')
overall_result_updated['Pe_En_Date'] = pd.to_datetime(overall_result_updated['Pe_En_Date'], format='%d-%m-%Y %H:%M')
overall_result_updated['Ce_Ex_Date'] = pd.to_datetime(overall_result_updated['Ce_Ex_Date'], format='%d-%m-%Y %H:%M')
overall_result_updated['Pe_Ex_Date'] = pd.to_datetime(overall_result_updated['Pe_Ex_Date'], format='%d-%m-%Y %H:%M')

## Function 11:
This function does the job which was described in the last note. The output is a dataframe which can be used to track the movement of equity throughout the year.

In [91]:
def track_equity(result_df, gain_df):
    value_df = pd.DataFrame(columns = ['Datetime', 'Equity_Value'])

    for i in range(len(gain_df.index)):
        curr_val = pd.DataFrame(columns = ['Datetime', 'Equity_Value'])
        curr_val.loc[i, 'Datetime'] = gain_df.loc[i, 'Datetime']
        curr_date = gain_df.loc[i, 'Datetime'].date()
        for j in range(len(result_df.index)):
            res_date = result_df.loc[j, 'Ce_En_Date'].date()
            if (curr_date == res_date):
                curr_equity_val = result_df.loc[j, 'Total_Capital_Return'] - result_df.loc[j, 'Total_Abs_Return']
                break
        curr_val.loc[i, 'Equity_Value'] = curr_equity_val + gain_df.loc[i, 'Pfolio_gain']
        value_df = pd.concat([value_df, curr_val], axis = 0, ignore_index=True)
    return value_df

Ensure the columns are of proper datatype to avoid errors.

In [92]:
gain_results['Datetime'] = pd.to_datetime(gain_results['Datetime'], format='%Y-%m-%d %H:%M:%S')

In [93]:
gain_results.dtypes

Datetime           datetime64[ns]
Gain_call_short            object
Gain_call_long             object
Gain_put_short             object
Gain_put_long              object
Pfolio_gain                object
dtype: object

In [94]:
eq_val_df = track_equity(overall_result_updated, gain_results)

In [108]:
eq_val_df

Datetime Equity_Value        Date
0     2017-01-02 10:30:00    1000000.0  2017-01-02
1     2017-01-02 10:31:00    999995.45  2017-01-02
2     2017-01-02 10:32:00    999996.65  2017-01-02
3     2017-01-02 10:33:00     999998.1  2017-01-02
4     2017-01-02 10:34:00    999996.05  2017-01-02
...                   ...          ...         ...
71581 2017-12-29 15:16:00    1094240.0  2017-12-29
71582 2017-12-29 15:17:00   1094241.35  2017-12-29
71583 2017-12-29 15:18:00    1094242.4  2017-12-29
71584 2017-12-29 15:19:00    1094242.2  2017-12-29
71585 2017-12-29 15:20:00   1094243.25  2017-12-29

[71586 rows x 3 columns]

Here, the Equity_Value column can be used to graph the evolution of equity. However, it will be slightly inaccurate. The accurate candlestick chart is made in a separate notebook, to keep this notebook short.

In [109]:
eq_val_df['Datetime'] = pd.to_datetime(eq_val_df['Datetime'], format='%Y-%m-%d %H:%M:%S')

In [131]:
fig = px.line(eq_val_df, x=eq_val_df['Datetime'], y='Equity_Value', title='Evolution of Equity')
fig.show()


C:\Users\thaku\anaconda3\Lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



As can be seen, there are some discontinuities present. This can be traced back to the fact that put and call options datasets were not equal.

In [132]:
eq_val_df.to_csv('equity_value.csv', index=False)

## The final notebook contains code for calculating the drawdown. 